In [1]:
import polars as pl
import pandas as pd
import numpy as np
import math as math
# find a better way to import?
import sys
import os
sys.path.append(os.path.join(os.path.dirname(''), '..'))

from constants import *


In [2]:
# read all data
players = pl.read_csv('../nfl-big-data-bowl-2024/players.csv')
plays = pl.read_csv('../nfl-big-data-bowl-2024/plays.csv',infer_schema_length=100000)
games = pl.read_csv('../nfl-big-data-bowl-2024/games.csv',infer_schema_length=10000)
tracking = pl.read_csv('../nfl-big-data-bowl-2024/tracking_week*.csv',infer_schema_length=10000)

In [3]:
# normalize data
players = players.with_columns([pl.col('nflId').cast(str)])
plays = plays.join(games,on='gameId')
plays = plays.with_columns([
    (pl.col('gameId').cast(str) + '-'
     + pl.col('playId').cast(str)).alias('uniquePlayId')
])

tracking = tracking.with_columns(
    (pl.col('gameId').cast(str) + '-'
     + pl.col('playId').cast(str)).alias('uniquePlayId'),
    (pl.col('gameId').cast(str) + '-'
     + pl.col('playId').cast(str) + '-'
     + pl.col('nflId').cast(str)).alias('uniquePlayerId'),
)

# normalize position
tracking=tracking.with_columns([
    pl.when(pl.col('playDirection')=='right').then(53.3-pl.col('y')).otherwise(pl.col('y')).alias('adjustedX'),
    pl.when(pl.col('playDirection')=='right').then(pl.col('x')).otherwise(120-pl.col('x')).alias('adjustedY')
])

tracking=tracking.with_columns([
    pl.when(pl.col('event')=='ball_snap').then(pl.col('frameId')).otherwise(-1).alias('startingFrameId'),
])
tracking=tracking.with_columns([
    pl.col('startingFrameId').max().over(pl.col('uniquePlayId')),
])
tracking=tracking.with_columns([
    (pl.col('frameId') - pl.col('startingFrameId')).alias('framesSinceSnap'),
])

# normalize orientation 'o' and direction 'dir'
# convert 'NA' to 0
replacement_values = {'NA': '0'}
tracking = tracking.with_columns(
    pl.col('o').apply(lambda x: replacement_values.get(x, x)),
    pl.col('dir').apply(lambda x: replacement_values.get(x, x)),
)

tracking=tracking.with_columns([
    pl.when(pl.col('playDirection')=='right').then(pl.col('dir').cast(pl.Float64)).otherwise(180-pl.col('dir').cast(pl.Float64)).alias('adjustedDir'),
    pl.when(pl.col('playDirection')=='right').then(pl.col('o').cast(pl.Float64)).otherwise((180+pl.col('o').cast(pl.Float64))%360).alias('adjustedO'),
])

In [4]:
CONE_ANGLE = 25 # degrees
MAX_DISTANCE = 6 # yards
BLOCKING_RADIUS = 1 # yards

# row = [o, dir, adjustedX, adjustedY, oDefender, dirDefender, adjustedXDefender, adjustedYDefender]
def looking_to_block_or_blocking_df_fn(row) -> int:
    blocking_status = 0
    player1 = row[0:4]
    player2 = row[4:]

    if is_in_vision_cone(player1, player2):
        blocking_status = 1

    if is_blocking(player1, player2):
        blocking_status = 2

    return blocking_status
    

def looking_to_block_or_blocking(player1: tuple, player2: tuple) -> int:
    if is_in_vision_cone(player1, player2):
        if is_blocking(player1, player2):
            return 2
            
        return 1

    return 0

def is_in_vision_cone(player1: tuple, player2: tuple) -> bool:
    return (is_in_angle(player1, player2) and is_in_distance(player1, player2))

def is_in_angle(player1: tuple, player2: tuple) -> bool:
    half_cone_angle = CONE_ANGLE / 2

    y_dist = player2[3] - player1[3]
    x_dist = player2[2] - player1[2]
    player1_orientation = float(player1[0]) if type(player1[0]) == str else player1[0]

    # print("isinangle")
    # print("player1")
    # print(player1)

    # print("player2")
    # print(player2)

    # print("player1_ori")
    # print(player1_orientation)

    angle = math.degrees(math.atan2(y_dist, x_dist))

    # print("angle")
    # print(angle)

    if player1_orientation - half_cone_angle <= angle <= player1_orientation + half_cone_angle:
        return True
    
    return False

def is_in_distance(player1: tuple, player2: tuple) -> bool:
    distance_between_players = calculate_distance(player1, player2)
    if distance_between_players <= MAX_DISTANCE:
        return True
    
    return False

def is_blocking(player1: tuple, player2: tuple) -> bool:
    distance_between_players = calculate_distance(player1, player2)
    if distance_between_players <= BLOCKING_RADIUS:
        return True

    return False


def calculate_distance(player1: tuple, player2: tuple) -> float:
    y_dist = abs(player1[3] - player2[3])
    x_dist = abs(player1[2] - player2[2])

    return math.sqrt(x_dist**2 + y_dist**2)

In [5]:
# This is just for testing - when we go for it we'll want to let it go against everything
labeled = tracking.filter(pl.col('gameId')==2022091104)


In [6]:
players = labeled.join(players,on='nflId',how='left')
players = players.join(games.select(['gameId','homeTeamAbbr','visitorTeamAbbr']),on='gameId')
players = players.with_columns([
    pl.when(pl.col('club')==pl.col('homeTeamAbbr'))
    .then(pl.col('visitorTeamAbbr'))
    .otherwise(pl.col('homeTeamAbbr'))
    .alias('opponentClub')
])


In [7]:
players = players.join(
    players,
    left_on=['gameId','playId','frameId','club'],
    right_on=['gameId','playId','frameId','opponentClub'],
    suffix='Defender'
)

In [8]:
blocking_df = players.select(
    'adjustedO', 'adjustedDir', 'adjustedX', 'adjustedY', 'adjustedODefender', 'adjustedDirDefender', 'adjustedXDefender', 'adjustedYDefender'
).apply(looking_to_block_or_blocking_df_fn)

isinangle
player1
(30.629999999999995, 149.57999999999998, 30.71, 26.909999999999997)
player2
(349.0, 145.27, 34.47, 29.650000000000006)
player1_ori
30.629999999999995
isinangle
player1
(105.66000000000003, 132.77, 28.02, 26.22)
player2
(349.0, 145.27, 34.47, 29.650000000000006)
player1_ori
105.66000000000003
isinangle
player1
(11.509999999999991, -13.909999999999997, 28.42, 37.709999999999994)
player2
(349.0, 145.27, 34.47, 29.650000000000006)
player1_ori
11.509999999999991
isinangle
player1
(226.47, -174.52999999999997, 33.75, 30.17)
player2
(349.0, 145.27, 34.47, 29.650000000000006)
player1_ori
226.47
isinangle
player1
(168.03999999999996, -138.04000000000002, 27.46, 46.78)
player2
(349.0, 145.27, 34.47, 29.650000000000006)
player1_ori
168.03999999999996
isinangle
player1
(281.0, -133.27999999999997, 41.78, 34.84)
player2
(349.0, 145.27, 34.47, 29.650000000000006)
player1_ori
281.0
isinangle
player1
(108.63, -21.689999999999998, 15.07, 28.540000000000006)
player2
(349.0, 145.27, 34.

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)




isinangle
player1
(146.14, 117.86, 17.779999999999994, 72.28)
player2
(272.59, 250.76, 51.809999999999995, 66.69)
player1_ori
146.14
isinangle
player1
(220.98, 217.87, 52.58, 62.34)
player2
(272.59, 250.76, 51.809999999999995, 66.69)
player1_ori
220.98
isinangle
player1
(134.81, 121.15, 29.539999999999996, 49.45)
player2
(272.59, 250.76, 51.809999999999995, 66.69)
player1_ori
134.81
isinangle
player1
(36.28, 46.94, 33.01, 44.63)
player2
(266.17, 249.47, 51.949999999999996, 66.31)
player1_ori
36.28
isinangle
player1
(114.56, 226.84, 33.15, 47.5)
player2
(266.17, 249.47, 51.949999999999996, 66.31)
player1_ori
114.56
isinangle
player1
(136.76, 111.06, 30.019999999999996, 48.28)
player2
(266.17, 249.47, 51.949999999999996, 66.31)
player1_ori
136.76
isinangle
player1
(247.98, 329.93, 22.119999999999997, 60.75)
player2
(266.17, 249.47, 51.949999999999996, 66.31)
player1_ori
247.98
isinangle
player1
(104.08, 126.63, 33.11, 43.18)
player2
(266.17, 249.47, 51.949999999999996, 66.31)
player1_or

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



isinangle
player1
(134.7, -24.129999999999995, 1.63, 110.91)
player2
(110.99000000000001, -63.27000000000001, 25.25, 103.71000000000001)
player1_ori
134.7
isinangle
player1
(339.91999999999996, -140.49, 46.43, 113.89)
player2
(110.99000000000001, -63.27000000000001, 25.25, 103.71000000000001)
player1_ori
339.91999999999996
isinangle
player1
(266.73, 92.79, 36.48, 109.99)
player2
(110.99000000000001, -63.27000000000001, 25.25, 103.71000000000001)
player1_ori
266.73
isinangle
player1
(0.6200000000000045, -4.8799999999999955, 18.11, 108.33)
player2
(110.99000000000001, -63.27000000000001, 25.25, 103.71000000000001)
player1_ori
0.6200000000000045
isinangle
player1
(95.12, -126.10000000000002, 45.33, 117.48)
player2
(110.99000000000001, -63.27000000000001, 25.25, 103.71000000000001)
player1_ori
95.12
isinangle
player1
(16.5, -20.99000000000001, 15.84, 104.71000000000001)
player2
(110.99000000000001, -63.27000000000001, 25.25, 103.71000000000001)
player1_ori
16.5
isinangle
player1
(38.590000

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



PanicException: python function failed KeyboardInterrupt: 

In [ ]:
blocking_df = blocking_df.to_series()

In [ ]:
players = players.with_columns(blockType=blocking_df)

In [20]:
test = pl.read_parquet('../labeledDataAttempt/labeledBlocks.parquet')

In [21]:
blocking_df = players.select(
    'adjustedO', 'adjustedDir', 'adjustedX', 'adjustedY', 'adjustedODefender', 'adjustedDirDefender', 'adjustedXDefender', 'adjustedYDefender'
).apply(looking_to_block_or_blocking_df_fn)

blocking_df = blocking_df.to_series()

players = players.with_columns(blockType=blocking_df)

In [22]:
test.filter(pl.col('displayName')=="Frank Ragnow").filter(pl.col('displayNameDefender')=="Kyzir White").filter(pl.col('gameId')==2022091104).select(pl.col('adjustedX'), pl.col('adjustedY'), pl.col('adjustedXDefender'), pl.col('adjustedYDefender'), pl.col('blockType'), pl.col('framesSinceSnap'), pl.col('playId')).filter(pl.col('framesSinceSnap')==3)

shape: (2, 7)
┌───────────┬───────────┬───────────────────┬───────────────────┬───────────┬─────────────────┬────────┐
│ adjustedX ┆ adjustedY ┆ adjustedXDefender ┆ adjustedYDefender ┆ blockType ┆ framesSinceSnap ┆ playId │
│ ---       ┆ ---       ┆ ---               ┆ ---               ┆ ---       ┆ ---             ┆ ---    │
│ f64       ┆ f64       ┆ f64               ┆ f64               ┆ i32       ┆ i64             ┆ i64    │
╞═══════════╪═══════════╪═══════════════════╪═══════════════════╪═══════════╪═════════════════╪════════╡
│ 23.38     ┆ 33.52     ┆ 21.43             ┆ 38.93             ┆ 1         ┆ 3               ┆ 86     │
│ 23.99     ┆ 83.42     ┆ 24.94             ┆ 88.3              ┆ 0         ┆ 3               ┆ 107    │
└───────────┴───────────┴───────────────────┴───────────────────┴───────────┴─────────────────┴────────┘

In [25]:
myData = players.filter(pl.col('displayName')=="Frank Ragnow").filter(pl.col('gameId')==2022091104).filter(pl.col('displayNameDefender')=="Kyzir White").filter(pl.col('playId')==86)
myData = myData.filter(pl.col('framesSinceSnap')==3)


blocking = myData.select(
    'adjustedO', 'adjustedDir', 'adjustedX', 'adjustedY', 'adjustedODefender', 'adjustedDirDefender', 'adjustedXDefender', 'adjustedYDefender'
).apply(looking_to_block_or_blocking_df_fn)

blocking

isinangle
player1
(437.55, -32.379999999999995, 23.38, 33.519999999999996)
player2
(267.58, 141.97, 21.43, 38.93000000000001)
player1_ori
437.55


shape: (1, 1)
┌───────┐
│ apply │
│ ---   │
│ i64   │
╞═══════╡
│ 0     │
└───────┘